In [1]:
import h5py
import os
import sys
import numpy as np
import matplotlib.pyplot as plt
%matplotlib inline

sys.path.append('/eagle/MDClimSim/mjp5595/ml4dvar/stormer/')
from stormer_utils_pangu import StormerWrapperPangu
from varsStormer import varsStormer

sys.path.append('/eagle/MDClimSim/mjp5595/ml4dvar/')
sys.path.append('/eagle/MDClimSim/mjp5595/ml4dvar/src')
from obs_cummulative import *

/home/mjp5595/.conda/envs/climaX/lib/python3.8/site-packages/torchvision/io/image.py:13: UserWarning: Failed to load image Python extension: libtorch_cuda_cu.so: cannot open shared object file: No such file or directory
  warn(f"Failed to load image Python extension: {e}")
/home/mjp5595/.conda/envs/climaX/lib/python3.8/site-packages/transformers/utils/generic.py:441: UserWarning: torch.utils._pytree._register_pytree_node is deprecated. Please use torch.utils._pytree.register_pytree_node instead.
  _torch_pytree._register_pytree_node(


In [9]:
def read_era5(data,vars_stormer):
    data_np = np.zeros((len(vars_stormer),128,256))
    for i,var in enumerate(vars_stormer):
        data_np[i] = data['input/{}'.format(var)][:]
    return data_np

vars_stormer = varsStormer().vars_stormer
vars_units = varsStormer().var_units

In [10]:
irga_obs = h5py.File("/eagle/MDClimSim/mjp5595/ml4dvar/obs/igra_141520_stormer_obs_standardized_360_3.hdf5")

temp_vals = irga_obs['2014/01/01/00/2m_temperature'][:]
h_idxs = irga_obs['2014/01/01/00/2m_temperature_H'][:,0]
h_obs = irga_obs['2014/01/01/00/2m_temperature_H'][:,1]

In [11]:
print('temp_vals[:,0] (lat) shape/min/max : {}/{}/{}'.format(temp_vals[:,0].shape,np.min(temp_vals[:,0]),np.max(temp_vals[:,0])))
print('temp_vals[:,1] (lon) shape/min/max : {}/{}/{}'.format(temp_vals[:,1].shape,np.min(temp_vals[:,1]),np.max(temp_vals[:,1])))
print('temp_vals[:,2] (val) shape/min/max : {}/{}/{}'.format(temp_vals[:,2].shape,np.min(temp_vals[:,2]),np.max(temp_vals[:,2])))
print('h_idxs shape/min/max : {}/{}/{}'.format(h_idxs.shape,np.min(h_idxs),np.max(h_idxs)))
print('h_obs shape/min/max : {}/{}/{}'.format(h_obs.shape,np.min(h_obs),np.max(h_obs)))

temp_vals[:,0] (lat) shape/min/max : (585,)/-77.85/82.5
temp_vals[:,1] (lon) shape/min/max : (585,)/0.31689999999997553/358.1183
temp_vals[:,2] (val) shape/min/max : (585,)/-2.5862019583703333/1.5012732172549814
h_idxs shape/min/max : (2340,)/2166.0/31700.0
h_obs shape/min/max : (2340,)/8.256790123450179e-05/0.9815403456790183


In [12]:
print('h_idxs[:4] :',h_idxs[:4])
h_idxs_unraveled = np.unravel_index(h_idxs[:4].astype('int'),(128,256))
print('h_idxs_unraveled :',h_idxs_unraveled)
print('h_obs[:4] :',h_obs[:4])
print('sum(h_obs[:4]) :',np.sum(h_obs[:4]))

h_idxs[:4] : [2166. 2422. 2167. 2423.]
h_idxs_unraveled : (array([8, 9, 8, 9]), array([118, 118, 119, 119]))
h_obs[:4] : [0.41405369 0.06740409 0.44594631 0.07259591]
sum(h_obs[:4]) : 1.0


In [13]:
# Rewrote this in ERA5_dense_obs.py
#
#import torch
#
#irga_obs = h5py.File("/eagle/MDClimSim/mjp5595/ml4dvar/obs/igra_141520_stormer_obs_standardized_360_3.hdf5")
#
#era5_dir = '/eagle/MDClimSim/tungnd/data/wb2/1.40625deg_from_full_res_1_step_6hr_h5df/train/'
#era5_2020_dir = '/eagle/MDClimSim/tungnd/data/wb2/1.40625deg_from_full_res_1_step_6hr_h5df/test/'
#
#lats = np.linspace(-90,90,128)
#lons = np.linspace(0,360,256)
#
#means = np.load('/eagle/MDClimSim/tungnd/data/wb2/1.40625deg_from_full_res_1_step_6hr_h5df/normalize_mean.npz')
#stds = np.load('/eagle/MDClimSim/tungnd/data/wb2/1.40625deg_from_full_res_1_step_6hr_h5df/normalize_std.npz')
#
##era5_obs = h5py.File('/eagle/MDClimSim/mjp5595/ml4dvar/data/era5_obs.h5', 'a')
#with h5py.File('/eagle/MDClimSim/mjp5595/ml4dvar/obs/era5_obs.h5', 'w') as era5_obs:
#    for year in ['2014','2015','2020']:
#        yr_grp = era5_obs.require_group(year)
#        year_hr_idx = 0
#        for month in list(irga_obs['{}'.format(year)].keys()):
#            mth_grp = era5_obs['{}'.format(year)].require_group(str(month))
#            for day in list(irga_obs['{}/{}'.format(year,month)].keys()):
#                day_grp = era5_obs['{}/{}'.format(year,month)].require_group(day)
#                for hour in list(irga_obs['{}/{}/{}'.format(year,month,day)].keys()):
#                    if int(hour) % 6 != 0:
#                        continue
#
#                    print('{}/{}/{}/{} - {:0>4d}'.format(year,month,day,hour,year_hr_idx))
#                    hr_group = era5_obs['{}/{}/{}'.format(year,month,day)].require_group(hour)
#
#                    # load era5
#                    if year == '2014' or year == '2015':
#                        try:
#                            era5_data = torch.from_numpy(read_era5(h5py.File(os.path.join(era5_dir,'{}_{:0>4d}.h5'.format(year,year_hr_idx))),vars_stormer))
#                        except:
#                            continue
#                    else:
#                        try:
#                            era5_data = torch.from_numpy(read_era5(h5py.File(os.path.join(era5_2020_dir,'{}_{:0>4d}.h5'.format(year,year_hr_idx))),vars_stormer))
#                        except:
#                            continue
#                    year_hr_idx += 1
#
#                    for var_idx,var in enumerate(vars_stormer):
#                        if var_idx != 0:
#                            continue
#
#                        era5_var_data = []
#                        era5_var_data_H = []
#                        for row in range(127):
#                            for col in range(255):
#                                era5_var_loc_data = era5_data[var_idx,row,col] \
#                                    + era5_data[var_idx,row+1,col] \
#                                    + era5_data[var_idx,row,col+1] \
#                                    + era5_data[var_idx,row+1,col+1]
#                                era5_var_loc_data = era5_var_loc_data / 4.
#                                era5_var_loc_data_lat = (row+1)*(180./128.) - 90.
#                                era5_var_loc_data_lon = (col+1)*(360./256.)
#                                era5_var_data.append([era5_var_loc_data_lat,
#                                                      era5_var_loc_data_lon,
#                                                      era5_var_loc_data])
#
#                                era5_var_loc_data_H_idx = np.zeros(4)
#                                era5_var_loc_data_H_idx[0] = np.ravel_multi_index([row,col],(128,256))
#                                era5_var_loc_data_H_idx[1] = np.ravel_multi_index([row+1,col],(128,256))
#                                era5_var_loc_data_H_idx[2] = np.ravel_multi_index([row,col+1],(128,256))
#                                era5_var_loc_data_H_idx[3] = np.ravel_multi_index([row+1,col+1],(128,256))
#                                era5_var_loc_data_H_obs = np.array([0.25,0.25,0.25,0.25])
#                                era5_var_data_H.extend(np.stack((era5_var_loc_data_H_idx,
#                                                                era5_var_loc_data_H_obs),
#                                                                axis=1)
#                                )
#
#                                #print()
#                                #print('col :',col)
#                                #print('era5_var_data :',era5_var_data)
#                                #print('era5_var_data_H[-4:] :',era5_var_data_H[-4:])
#
#                        era5_var_data = np.array(era5_var_data)
#                        era5_var_data_H = np.array(era5_var_data_H)
#                        #print('era5_var_data.shape :',era5_var_data.shape)
#                        #print('era5_var_data_H.shape :',era5_var_data_H.shape)
#                        era5_var_data[:,2] = (era5_var_data[:,2] - means[var]) / stds[var]
#
#                        #print()
#                        #print('era5_var_data :',era5_var_data)
#                        #print('era5_var_data_H :',era5_var_data_H)
#
#                        era5_obs_dataset = era5_obs['{}/{}/{}/{}'.format(year,month,day,hour)].create_dataset(
#                            '{}'.format(var), data=era5_var_data, dtype = 'f8'
#                        )
#                        era5_obs_dataset_H = era5_obs['{}/{}/{}/{}'.format(year,month,day,hour)].create_dataset(
#                            '{}_H'.format(var), data=era5_var_data_H, dtype = 'f8'
#                        )

In [2]:
import h5py
import os

dense_obs_dir = '/eagle/MDClimSim/mjp5595/ml4dvar/obs/'
dense_obs_prefix = 'era5_dense_obs_2014'
#dense_obs_combined = h5py.File(os.path.join(dense_obs_dir,'era5_obs_dense_2014.h5'),'w')
with h5py.File(os.path.join(dense_obs_dir,'era5_obs_dense_2014.h5'),'w') as dense_obs_combined:
    # There are 69 vars for stormer
    for i in range(69):
        #dense_obs_var_data = h5py.File(os.path.join(dense_obs_dir,dense_obs_prefix+'-{}.h5'.format(i)),'r')
        with h5py.File(os.path.join(dense_obs_dir,dense_obs_prefix+'-{}.h5'.format(i)),'r') as dense_obs_var_data:

            for year in ['2014']:
                yr_grp = dense_obs_combined.require_group(year)
                for month in list(dense_obs_var_data['{}'.format(year)].keys()):
                    mth_grp = dense_obs_combined['{}'.format(year)].require_group(str(month))
                    for day in list(dense_obs_var_data['{}/{}'.format(year,month)].keys()):
                        day_grp = dense_obs_combined['{}/{}'.format(year,month)].require_group(day)
                        for hour in list(dense_obs_var_data['{}/{}/{}'.format(year,month,day)].keys()):
                            if int(hour) % 6 != 0:
                                continue
                            if int(month) > 4:
                                continue
                            
                            hour_grp = dense_obs_combined['{}/{}/{}'.format(year,month,day)].require_group(hour)
                            for var_key in dense_obs_var_data['{}/{}/{}/{}'.format(year,month,day,hour)].keys():
                                #var_grp = dense_obs_combined['{}/{}/{}/{}'.format(year,month,day,hour)].require_group(var_key)

                                var_data = dense_obs_var_data['{}/{}/{}/{}/{}'.format(year,month,day,hour,var_key)][:]
                                print('{}/{}/{}/{}/{} - {}'.format(year,month,day,hour,var_key,var_data.shape))
                                var_dataset = dense_obs_combined['{}/{}/{}/{}'.format(year,month,day,hour)].create_dataset(
                                    '{}'.format(var_key), data=var_data, dtype = 'f8'
                                )

2014/01/01/00/2m_temperature
var_data.shape : (32385, 3)
2014/01/01/00/2m_temperature_H
var_data.shape : (129540, 2)
2014/01/01/06/2m_temperature
var_data.shape : (32385, 3)
2014/01/01/06/2m_temperature_H
var_data.shape : (129540, 2)
2014/01/01/12/2m_temperature
var_data.shape : (32385, 3)
2014/01/01/12/2m_temperature_H
var_data.shape : (129540, 2)
2014/01/01/18/2m_temperature
var_data.shape : (32385, 3)
2014/01/01/18/2m_temperature_H
var_data.shape : (129540, 2)
2014/01/02/00/2m_temperature
var_data.shape : (32385, 3)
2014/01/02/00/2m_temperature_H
var_data.shape : (129540, 2)
2014/01/02/06/2m_temperature
var_data.shape : (32385, 3)
2014/01/02/06/2m_temperature_H
var_data.shape : (129540, 2)
2014/01/02/12/2m_temperature
var_data.shape : (32385, 3)
2014/01/02/12/2m_temperature_H
var_data.shape : (129540, 2)
2014/01/02/18/2m_temperature
var_data.shape : (32385, 3)
2014/01/02/18/2m_temperature_H
var_data.shape : (129540, 2)
2014/01/03/00/2m_temperature
var_data.shape : (32385, 3)
2014/01

In [3]:
dense_obs_combined = h5py.File(os.path.join(dense_obs_dir,'era5_obs_dense_2014.h5'),'r')

In [4]:
dense_obs_combined.keys()

<KeysViewHDF5 ['2014']>

In [6]:
dense_obs_combined = h5py.File('/eagle/MDClimSim/mjp5595/ml4dvar/obs/era5_obs_dense_2014.h5')
print('len(keys) :',len(dense_obs_combined['2014/01/01/00'].keys()))
print('shape :',dense_obs_combined['2014/01/01/00/2m_temperature'].shape)

len(keys) : 138
shape : (32385, 3)
